In [2]:
import pandas as pd
import navis
import os
import trimesh
import rtree
from joblib import Parallel, delayed
from joblib import parallel_backend
from tqdm import tqdm


# Read ALPN IDs from CSV
oneN_ids = pd.read_csv('../1N_ids.csv')

# Read previouslyfiltered synapses from CSV
syn_df = pd.read_csv('./input/filtered_1N_synapses.csv')

In [4]:
# Load all .ply mesh files
meshes = {}
glom_names = []
mesh_dir = './glom_meshes_proc'
for mesh_file in os.listdir(mesh_dir):
    if mesh_file.endswith('.ply'):
        glom_name = mesh_file.replace('.ply', '')
        glom_names.append(glom_name)
        meshes[glom_name] = navis.read_mesh(os.path.join(mesh_dir, mesh_file))

# Filter synapses to only include those where post_pt_root_id matches alpn_ids
oneN_syn_df = syn_df[syn_df['pre_pt_root_id'].isin(oneN_ids['root_id'])]
# Initialize new columns for each glomerulus with 0s
for glom in glom_names:
    oneN_syn_df.loc[:, glom] = 0

print(oneN_syn_df.columns)

Index(['id', 'pre_pt_root_id', 'post_pt_root_id', 'connection_score',
       'cleft_score', 'gaba', 'ach', 'glut', 'oct', 'ser',
       ...
       'VP2_L', 'VP2_R', 'VP3_L', 'VP3_R', 'VP4_L', 'VP4_R', 'VP5_L', 'VP5_R',
       'V_L', 'V_R'],
      dtype='object', length=134)


C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\2631403262.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oneN_syn_df.loc[:, glom] = 0
C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\2631403262.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  oneN_syn_df.loc[:, glom] = 0
C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\2631403262.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the cave

In [6]:
i = 1
# Iterate through each row in the dataframe
for idx, row in oneN_syn_df.iterrows():
    try:
        # Get point coordinates for current row
        point = row[['pre_pt_position_x', 'pre_pt_position_y', 'pre_pt_position_z']].values
        print(point)
        print(i)
        i += 1
        # Check each glomerulus mesh
        for glom_name, mesh in meshes.items():
            # Check if point is inside this glomerulus mesh
            trimesh_mesh = mesh.trimesh # Access Trimesh object because contains method not working for navis meshes
            if trimesh_mesh.contains([point])[0]:
                # Set the corresponding glomerulus column to 1 
                oneN_syn_df.loc[idx, glom_name] = 1
    except IndexError:
        print(f"Index error occurred at idx {idx}")
        continue

[467680 262488 74440]
1
[479736 255204 74520]
2
[458052 255104 75040]
3
[573404 287780 61720]
4
[588340 243760 67320]
5
[587360 284176 67440]
6
[599156 249432 68160]
7
[585216 247320 67600]
8
[580000 257676 68160]
9
[483604 250236 80240]
10
[462012 260160 92960]
11
[553320 228576 72840]
12
[569584 277400 78920]
13
[453872 261404 78000]
14
[449428 254936 88560]
15
[486000 268792 87200]
16
[490516 260880 86920]
17
[591232 238692 41760]
18
[453864 240524 84720]
19
[466952 235536 65560]
20
[581312 252032 66080]
21
[477608 260244 65880]
22
[466964 258268 65680]
23
[458076 268976 76480]
24
[456716 251992 89800]
25
[453884 261124 94680]
26
[490936 242512 70720]
27
[586156 282064 71320]
28
[559128 259884 71480]
29
[484812 259164 71520]
30
[468512 239264 82320]
31
[458864 237856 82040]
32
[476200 262764 80760]
33
[455700 251132 81120]
34
[585320 270228 65160]
35
[584752 280340 64000]
36
[459108 257612 50960]
37
[588372 266204 61480]
38
[589168 251016 62160]
39
[586168 257328 61800]
40
[472228 2

In [8]:
oneN_syn_df.to_csv('1N_glomeruli_output.csv', index=False)

# Group by 'post_pt_root_id' and sum all other columns.
summed_df = oneN_syn_df.groupby('pre_pt_root_id').sum(numeric_only=True).reset_index()

# Display the resulting dataframe.
summed_df.head()
summed_df.to_csv('1N_glomeruli_output_sum.csv', index=False)

In [5]:
# Read olfactory IDs from CSV
twoN_ids = pd.read_csv('../2N_ids.csv')

# Read previously filtered olfactory 3N synapses from CSV
syn_df_2 = pd.read_csv('./input/filtered_2N_synapses.csv')

# Filter synapses to only include those where post_pt_root_id matches olfactory_ids
twoN_syn_df = syn_df_2[syn_df_2['pre_pt_root_id'].isin(twoN_ids['root_id'])]
# Initialize new columns for each glomerulus with 0s
for glom in glom_names:
    twoN_syn_df.loc[:, glom] = 0

print(twoN_syn_df.columns)

C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\3636580575.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  twoN_syn_df.loc[:, glom] = 0
C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\3636580575.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  twoN_syn_df.loc[:, glom] = 0
C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\3636580575.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the cave

Index(['id', 'pre_pt_root_id', 'post_pt_root_id', 'connection_score',
       'cleft_score', 'gaba', 'ach', 'glut', 'oct', 'ser',
       ...
       'VP2_L', 'VP2_R', 'VP3_L', 'VP3_R', 'VP4_L', 'VP4_R', 'VP5_L', 'VP5_R',
       'V_L', 'V_R'],
      dtype='object', length=134)


C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\3636580575.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  twoN_syn_df.loc[:, glom] = 0
C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\3636580575.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  twoN_syn_df.loc[:, glom] = 0
C:\Users\snkyl\AppData\Local\Temp\ipykernel_1672\3636580575.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all colu